## 1. BertBiz

In [3]:
from transformers import AutoTokenizer
from bertviz.transformers_neuron_view import BertModel
from bertviz.neuron_view import show

In [4]:
model_ckpt = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)
model = BertModel.from_pretrained(model_ckpt)
text = "time flies like an arrow"

show(model, "bert", tokenizer, text, display_mode="light", layer=0, head=8)

tokenizer_config.json: 100%|██████████| 28.0/28.0 [00:00<00:00, 9.25kB/s]
config.json: 100%|██████████| 570/570 [00:00<00:00, 514kB/s]
vocab.txt: 100%|██████████| 232k/232k [00:00<00:00, 583kB/s]
tokenizer.json: 100%|██████████| 466k/466k [00:00<00:00, 1.10MB/s]
100%|██████████| 440473133/440473133 [03:43<00:00, 1968094.45B/s] 


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## 2. Scaled Dot Product

In [6]:
inputs = tokenizer(text, return_tensors="pt", add_special_tokens=False)     # add_special_tokens=False (except [CLS], [SEP])
inputs.input_ids

tensor([[ 2051, 10029,  2066,  2019,  8612]])

In [7]:
from torch import nn
from transformers import AutoConfig

In [8]:
config = AutoConfig.from_pretrained(model_ckpt)
token_emb = nn.Embedding(config.vocab_size, config.hidden_size)
token_emb

Embedding(30522, 768)

In [10]:
inputs_embeds = token_emb(inputs.input_ids)
inputs_embeds.size()        # [batch_size, seq_len, hidden_dim]

torch.Size([1, 5, 768])

In [11]:
import torch
from math import sqrt

In [15]:
query = key = value = inputs_embeds
dim_k = key.size(-1)

In [21]:
# torch.bmm(query, key.transpose(1,2)).size()
sqrt(dim_k)

27.712812921102035

In [22]:
scores = torch.bmm(query, key.transpose(1,2)) / sqrt(dim_k)     # 표준편차를 1로 정규화
scores.size()

torch.Size([1, 5, 5])

In [13]:
import torch.nn.functional as F

In [14]:
weights = F.softmax(scores, dim=-1)
weights.sum(dim=-1)

tensor([[1., 1., 1., 1., 1.]], grad_fn=<SumBackward1>)

In [23]:
attn_outputs = torch.bmm(weights, value)
attn_outputs.shape

torch.Size([1, 5, 768])

In [24]:
def scaled_dot_product_attention(query, key, value):
    dim_k = query.size(-1)
    scores = torch.bmm(query, key.transpose(1, 2)) / sqrt(dim_k)
    weights = F.softmax(scores, dim=-1)

    return torch.bmm(weights, value)

## 3. Multi-Head Attention

In [26]:
class AttentionHead(nn.Module):
    def __init__(self, embed_dim, head_dim):
        super().__init__()
        self.q = nn.Linear(embed_dim, head_dim)
        self.k = nn.Linear(embed_dim, head_dim)
        self.v = nn.Linear(embed_dim, head_dim)

    def forward(self, hidden_state):
        attn_outputs = scaled_dot_product_attention(self.q(hidden_state), self.k(hidden_state), self.v(hidden_state))
        return attn_outputs

In [27]:
class MultiHeadAttention(nn.Module):
    def __init__(self, config):
        super().__init__()
        embed_dim = config.hidden_size
        num_heads = config.num_attention_heads
        head_dim = embed_dim // num_heads
        self.heads = nn.ModuleList(
            [AttentionHead(embed_dim, head_dim) for _ in range(num_heads)]
        )
        self.output_linear = nn.Linear(embed_dim, embed_dim)

    def forward(self, hidden_state):
        x = torch.cat([h(hidden_state) for h in self.heads], dim=-1)
        x = self.output_linear(x)
        return x

In [28]:
multihead_attn = MultiHeadAttention(config)
attn_output = multihead_attn(inputs_embeds)
attn_output.size()

torch.Size([1, 5, 768])

In [29]:
from bertviz import head_view
from transformers import AutoModel

In [30]:
model = AutoModel.from_pretrained(model_ckpt, output_attentions=True)

sentence_a = "time flies like an arrow"
sentence_b = "fruit flies like a banana"

viz_inputs = tokenizer(sentence_a, sentence_b, return_tensors="pt")
attention = model(**viz_inputs).attentions
sentence_b_start = (viz_inputs.token_type_ids==0).sum(dim=1)
tokens = tokenizer.convert_ids_to_tokens(viz_inputs.input_ids[0])

head_view(attention, tokens, sentence_b_start, heads=[8])

model.safetensors: 100%|██████████| 440M/440M [00:05<00:00, 81.5MB/s] 


<IPython.core.display.Javascript object>

## 4. Position-Wise Feed-Forward Network

In [31]:
class FeedForward(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.linear_1 = nn.Linear(config.hidden_size, config.intermediate_size)
        self.linear_2 = nn.Linear(config.intermediate_size, config.hidden_size)
        self.gelu = nn.GELU()
        self.dropout = nn.Dropout(config.hidden_dropout_prob)

    def forward(self, x):
        x = self.linear_1(x)
        x = self.gelu(x)
        x = self.linear_2(x)
        x = self.dropout(x)

        return x